# Speech enhancement

<div class="alert alert-info">

This tutorial is available as an IPython notebook at [malaya-speech/example/speech-enhancement](https://github.com/huseinzol05/malaya-speech/tree/master/example/speech-enhancement).
    
</div>

<div class="alert alert-info">

This module is language independent, so it save to use on different languages. Pretrained models trained on multilanguages.
    
</div>

<div class="alert alert-warning">

This is an application of malaya-speech Pipeline, read more about malaya-speech Pipeline at [malaya-speech/example/pipeline](https://github.com/huseinzol05/malaya-speech/tree/master/example/pipeline).
    
</div>

### Dataset

Trained on English, Manglish and Bahasa podcasts with augmented noises, gathered at https://github.com/huseinzol05/malaya-speech/tree/master/data/podcast

Purpose of this module to enhance voice activities, reduce reverberance, reduce loudness and broken voices.

**voice -> malaya-speech noise reduction -> malaya-speech speech enhancement**.

In [1]:
import malaya_speech
import numpy as np
from malaya_speech import Pipeline

In [2]:
y, sr = malaya_speech.load('speech/khutbah/wadi-annuar.wav', sr = 44100)
len(y), sr, len(y) / sr

(441000, 44100, 10.0)

So total length is 10 seconds.

In [3]:
import IPython.display as ipd
ipd.Audio(y[:10 * sr], rate = sr)

The speech got room echo and a bit of broken high pitch, because it recorded in mosque.

In [4]:
from glob import glob

wavs = glob('speech/enhance/*.wav')
wavs

['speech/enhance/461-y_.wav',
 'speech/enhance/125-y_.wav',
 'speech/enhance/371-y_.wav',
 'speech/enhance/328-y_.wav']

In [5]:
wavs = [malaya_speech.load(f, sr = None)[0] for f in wavs]

### List available deep enhance

In [6]:
malaya_speech.speech_enhancement.available_deep_enhance()

INFO:root:Only calculate SDR, ISR, SAR on voice sample. Higher is better.


Size (MB)  Quantized Size (MB)       SDR        ISR  \
unet-enhance-24       40.7                 10.3  9.877178  15.916217   
unet-enhance-36       91.3                 23.4  8.749694  14.512658   

                       SAR  
unet-enhance-24  13.709130  
unet-enhance-36  13.963656

### Load deep enhance

```python
def deep_enhance(
    model: str = 'unet-enhance-24', quantized: bool = False, **kwargs
):
    """
    Load Speech Enhancement UNET Waveform sampling deep learning model.

    Parameters
    ----------
    model : str, optional (default='unet-enhance-24')
        Model architecture supported. Allowed values:

        * ``'unet-enhance-24'`` - pretrained UNET Speech Enhancement 24 filter size.
        * ``'unet-enhance-36'`` - pretrained UNET Speech Enhancement 36 filter size.
    quantized : bool, optional (default=False)
        if True, will load 8-bit quantized model. 
        Quantized model not necessary faster, totally depends on the machine.

    Returns
    -------
    result : malaya_speech.model.tf.UNET1D class
    """
```

In [7]:
model = malaya_speech.speech_enhancement.deep_enhance(model = 'unet-enhance-24')
quantized_model = malaya_speech.speech_enhancement.deep_enhance(model = 'unet-enhance-24', 
                                                                quantized = True)


/Library/Frameworks/Python.framework/Versions/3.7/lib/python3.7/site-packages/tensorflow_core/python/client/session.py:1750: UserWarning: An interactive session is already active. This can cause out-of-memory errors in some cases. You must explicitly call `InteractiveSession.close()` to release resources held by the other session(s).
  warnings.warn('An interactive session is already active. This can '


### Important factor for deep enhance

1. Deep Enhance model trained on 22k sample rate, so make sure load the audio with 22k sample rate.

```python
malaya_speech.load(audio_file, sr = 22050)
librosa.load(audio_file, sr = 22050)
```

2. You can feed dynamic length of audio, no need to cap, the model do padding by itself. But again, the longer the audio, the longer time required to calculate, unless you have GPU to speed up.
3. The model process on waveform level, so no STFT or inverse STFT involved.

#### Predict

Speech Enhancement model only accept 1 audio for single feed-forward,

```python
def predict(self, input):
    """
    Enhance inputs, will return waveform.

    Parameters
    ----------
    input: np.array
        np.array or malaya_speech.model.frame.Frame.

    Returns
    -------
    result: np.array
    """
```

In [8]:
%%time

y_ = malaya_speech.resample(y, sr, 22050)

CPU times: user 15.1 ms, sys: 6.17 ms, total: 21.3 ms
Wall time: 20.1 ms


In [9]:
%%time

logits = model.predict(y_)

CPU times: user 2.45 s, sys: 718 ms, total: 3.17 s
Wall time: 815 ms


In [10]:
%%time

quantized_logits = quantized_model.predict(y_)

CPU times: user 2.41 s, sys: 710 ms, total: 3.12 s
Wall time: 752 ms


In [11]:
ipd.Audio(logits, rate = 22050)

In [12]:
ipd.Audio(quantized_logits, rate = 22050)

#### Try more example

In [27]:
%%time

logits = [model.predict(w) for w in wavs]

CPU times: user 4.31 s, sys: 1.06 s, total: 5.37 s
Wall time: 1.01 s


In [28]:
%%time

quantized_logits = [quantized_model.predict(w) for w in wavs]

CPU times: user 4.33 s, sys: 999 ms, total: 5.32 s
Wall time: 1.01 s


In [29]:
ipd.Audio(wavs[0], rate = 22050)

In [30]:
ipd.Audio(logits[0], rate = 22050)

In [31]:
ipd.Audio(wavs[1], rate = 22050)

In [32]:
ipd.Audio(logits[1], rate = 22050)

In [35]:
ipd.Audio(wavs[2], rate = 22050)

In [36]:
ipd.Audio(logits[2], rate = 22050)

In [37]:
ipd.Audio(wavs[3], rate = 22050)

In [38]:
ipd.Audio(logits[3], rate = 22050)

### List available masking model

Masking model is just simply mask STFT input to reduce echo, reverberance and broken pitch. This model cannot generate new waveform, eg, if input waveform is filtered using low / high frequency, this model cannot enhance the input. So, we prefer use `malaya_speech.speech_enhancement.deep_enhance`.

In [39]:
malaya_speech.speech_enhancement.available_deep_masking()

INFO:root:Only calculate SDR, ISR, SAR on voice sample. Higher is better.


Size (MB)  Quantized Size (MB)  SUM MAE  MAE_SPEAKER  MAE_NOISE  \
unet              78.9                 20.0  0.85896     0.468490   0.390460   
resnet-unet       91.4                 23.0  0.81540     0.447958   0.367441   

                   SDR       ISR        SAR  
unet         12.128050  14.67067  15.019682  
resnet-unet  12.349259  14.85418  15.217510

### Load masking model

```python
def deep_masking(model: str = 'resnet-unet', quantized: bool = False, **kwargs):
    """
    Load Speech Enhancement STFT UNET masking deep learning model.

    Parameters
    ----------
    model : str, optional (default='resnet-unet')
        Model architecture supported. Allowed values:

        * ``'unet'`` - pretrained UNET.
        * ``'resnet-unet'`` - pretrained resnet-UNET.
    quantized : bool, optional (default=False)
        if True, will load 8-bit quantized model. 
        Quantized model not necessary faster, totally depends on the machine.

    Returns
    -------
    result : malaya_speech.model.tf.UNETSTFT class
    """
```

In [1]:
model = malaya_speech.speech_enhancement.deep_masking(model = 'resnet-unet')

### Important factor for deep masking

1. Noise Reduction model trained on 44k sample rate, so make sure load the audio with 44k sample rate.

```python
malaya_speech.load(audio_file, sr = 44100)
librosa.load(audio_file, sr = 44100)
```

2. You can feed dynamic length of audio, no need to cap, the model do padding by itself. But again, the longer the audio, the longer time required to calculate, unless you have GPU to speed up.
3. STFT and Inverse STFT can be done on GPU level, so the model is really fast on GPU.

In [7]:
%%time

output = model(y)

CPU times: user 4.95 s, sys: 933 ms, total: 5.89 s
Wall time: 1.87 s


In [8]:
output

{'voice': array([1.9417714e-08, 2.0993056e-08, 2.4434440e-08, ..., 2.1756661e-01,
        1.9999057e-01, 1.4723262e-01], dtype=float32),
 'noise': array([-1.9704540e-08, -2.3319327e-08, -2.4154849e-08, ...,
         1.5757367e-01,  1.5660551e-01,  9.5091663e-02], dtype=float32)}

In [9]:
ipd.Audio(output['voice'], rate = sr)

In [11]:
%%time

output = model(malaya_speech.resample(wavs[0], 22050, 44100))

CPU times: user 4.22 s, sys: 723 ms, total: 4.94 s
Wall time: 810 ms


In [12]:
ipd.Audio(output['voice'], rate = sr)